In [2]:
import pandas as pd

cls = pd.read_excel("./CLS.xlsx", "Summary")

cls_data = cls.iloc[4:cls.shape[0],1:cls.shape[1]]
header =  cls.iloc[3].fillna("").astype('string') + ' : ' + cls.iloc[2].fillna("").astype('string')
cls_data.columns = header[1:cls.shape[1]]
cls_data.rename(columns = {'LA Code : ' : 'LA Code', 'LA Name : ': 'LA Name'}, inplace = True)
# Don't include RC11 because it's not a number
cls_data = cls_data.loc[:, cls_data.columns != 'RUC11 : ']
cls_data = cls_data.reset_index(drop = True)
cls_data = cls_data.dropna(subset = 'LA Code')
cls_data = cls_data.loc[cls_data['LA Code'].str.startswith('E')]
cls_data[cls_data.columns.difference(['LA Code', 'LA Name'])] = cls_data[cls_data.columns.difference(['LA Code', 'LA Name'])].astype('float64')

In [99]:
import json
deciles = pd.DataFrame(cls_data["LA Code"])
deciles_df = cls_data.apply(lambda col: pd.qcut(col, q = 10, labels = False, duplicates = 'drop') + 1 if col.dtype != 'object' else col)
deciles_dict = deciles_df.set_index('LA Code').to_dict(orient="index")
with open("deciles.json", "w") as f:
    json.dump(deciles_dict, f)
deciles_df

LA Code               LA Name  \
0    E06000053       Isles of Scilly   
1    E07000124         Ribble Valley   
2    E06000017               Rutland   
3    E07000044            South Hams   
4    E07000035      Derbyshire Dales   
..         ...                   ...   
291  E08000031         Wolverhampton   
292  E06000032                 Luton   
293  E09000002  Barking and Dagenham   
294  E09000025                Newham   
295  E06000039                Slough   

     How often do you feel lonely? : Often/Always  \
0                                               1   
1                                               3   
2                                               3   
3                                               4   
4                                               7   
..                                            ...   
291                                            10   
292                                            10   
293                                             9   
294                                             9   
295                                             9   

     Indirect Loneliness : Score of 8 or 9  \
0                                        1   
1                                        2   
2                                        2   
3                                        3   
4                                        4   
..                                     ...   
291                                      9   
292                                     10   
293                                      7   
294                                      8   
295                                     10   

     How strongly do you feel you belong to your immediate neighbourhood? : Total  \
0                                                   10                              
1                                                   10                              
2                                                   10                              
3                                                   10                              
4                                                   10                              
..                                                 ...                              
291                                                  2                              
292                                                  2                              
293                                                  1                              
294                                                  1                              
295                                                  1                              

     Do you think that over the past two years your area has… : Got better to live in  \
0                                                    6                                  
1                                                    6                                  
2                                                    2                                  
3                                                    4                                  
4                                                    5                                  
..                                                 ...                                  
291                                                  5                                  
292                                                  9                                  
293                                                 10                                  
294                                                 10                                  
295                                                  2                                  

     To what extent would you agree or disagree that people in your neighbourhood pull together to improve the neighbourhood? : Agree  \
0                                                   10                                                       

In [26]:
# distance from mean
import scipy.stats as stats
numeric_cols = cls_data.iloc[:, 2:]
column_means = numeric_cols.mean()
column_medians = numeric_cols.median()
column_stds = numeric_cols.std()
classified = numeric_cols.apply(
    lambda col : col.apply(
        lambda x: 1 if x > column_means[col.name] + column_stds[col.name]
        else -1 if x < column_means[col.name] - column_stds[col.name]
        else 0
    )
)
i_st_away = pd.concat([cls_data.iloc[:, :2], classified], axis = 1)
dist_from_mean = cls_data.iloc[:, 2:] - column_means
dists = pd.concat([cls_data.iloc[:, :2], dist_from_mean], axis = 1)
z_scores = numeric_cols.apply(
    lambda col: (col - column_means[col.name])/column_stds[col.name]
)
critical_z = stats.norm.ppf(0.975)
classified = z_scores.apply(
    lambda col: col.apply(
        lambda z: 1 if z > critical_z else -1 if z < -critical_z else 0
    )
)
stat_sig = pd.concat([cls_data.iloc[:, :2], classified], axis = 1)

rounded = numeric_cols.round(2)
rounded_medians = column_medians.round(2)
classified = rounded.apply(
    lambda col : col.apply(
        lambda x: 1 if x - 0.01 > rounded_medians[col.name]
        else -1 if x + 0.01 < rounded_medians[col.name]
        else 0
    )
)
rounded_above_below = pd.concat([cls_data.iloc[:, :2], classified], axis = 1)
rounded_above_below

LA Code               LA Name  \
0    E06000053       Isles of Scilly   
1    E07000124         Ribble Valley   
2    E06000017               Rutland   
3    E07000044            South Hams   
4    E07000035      Derbyshire Dales   
..         ...                   ...   
291  E08000031         Wolverhampton   
292  E06000032                 Luton   
293  E09000002  Barking and Dagenham   
294  E09000025                Newham   
295  E06000039                Slough   

     How often do you feel lonely? : Often/Always  \
0                                              -1   
1                                              -1   
2                                              -1   
3                                              -1   
4                                               0   
..                                            ...   
291                                             1   
292                                             1   
293                                             1   
294                                             1   
295                                             1   

     Indirect Loneliness : Score of 8 or 9  \
0                                       -1   
1                                       -1   
2                                       -1   
3                                        0   
4                                        0   
..                                     ...   
291                                      1   
292                                      1   
293                                      1   
294                                      1   
295                                      1   

     How strongly do you feel you belong to your immediate neighbourhood? : Total  \
0                                                    1                              
1                                                    1                              
2                                                    1                              
3                                                    1                              
4                                                    1                              
..                                                 ...                              
291                                                 -1                              
292                                                 -1                              
293                                                 -1                              
294                                                 -1                              
295                                                 -1                              

     Do you think that over the past two years your area has… : Got better to live in  \
0                                                    0                                  
1                                                    0                                  
2                                                   -1                                  
3                                                   -1                                  
4                                                   -1                                  
..                                                 ...                                  
291                                                  0                                  
292                                                  1                                  
293                                                  1                                  
294                                                  1                                  
295                                                 -1                                  

     To what extent would you agree or disagree that people in your neighbourhood pull together to improve the neighbourhood? : Agree  \
0                                                    1                                                       

In [27]:
import folium
import json

with open("LAD.geojson") as f:
    la_geo = json.load(f)
m = folium.Map()


triciles = pd.DataFrame(cls_data["LA Code"])
triciles_df = cls_data.apply(lambda col: pd.qcut(col, q = 3, labels = False, duplicates = 'drop') + 1 if col.dtype != 'object' else col)
triciles_dict = triciles_df.set_index('LA Code').to_dict(orient="index")

folium.GeoJson(la_geo, name = "hello_world").add_to(m)

folium.Choropleth(
    geo_data = la_geo,
    name = "choloropleth",
    data = rounded_above_below,
    columns = ['LA Code', 'To what extent would you agree or disagree that people in your neighbourhood pull together to improve the neighbourhood? : Agree'],
    key_on = 'feature.properties.LAD24CD',
    fill_color="YlGn",
    legend_name = "civic engagement tricile"
).add_to(m)
m.save("out.html")
m

In [59]:
import pandas as pd

def process_sheet(sheet_name, df):
    """
    Process an individual sheet:
    1. Check if column A contains "Question".
    2. Set the row with "Question" as the header.
    3. Pivot data to include "Question" and "answer".
    """
    # Step 1: Check if "Question" exists in column A
    col_a = df.iloc[:, 0]  # Column A
    question_row_idx = col_a[col_a == "Question"].index

    if len(question_row_idx) == 0:
        # Skip if no "Question" is found
        return None

    # Step 2: Check if "Local authority district" is two rows below "Question"
    question_row_idx = question_row_idx[0]
    local_auth_row_idx = question_row_idx + 2

    if (
        local_auth_row_idx >= len(df) or
        df.iloc[local_auth_row_idx, 0] != "Local authority district"
    ):
        # Skip if not found or out of bounds
        return None

    # Step 3: Set "Question" row as headers
    df.columns = df.iloc[question_row_idx]
    df = df.iloc[question_row_idx + 1:].reset_index(drop=True)

    # Extract the "text" and "answer" values (assumed to be in the first two columns)
    question_text = df.iloc[0, 0]
    question_answer = df.iloc[0, 1]

    # Retain rows starting from "Local authority district"
    df = df.iloc[1:].reset_index(drop=True)

    total_row = df.iloc[[0]]
    if not total_row.empty:
        eng_perc = total_row.iloc[0]["2023/24 Percentage (%)"]
        eng_low_perc = total_row.iloc[0]["2023/24 Lower Estimate percentage (%)"]
        eng_high_perc = total_row.iloc[0]["2023/24 Upper Estimate percentage (%)"]
    else:
        eng_perc, eng_low_perc, eng_high_perc = None

    # Add "text" and "answer" columns
    df["text"] = question_text
    df["answer"] = question_answer
    df["eng_perc"] = eng_perc
    df["eng_low_perc"] = eng_low_perc
    df["eng_high_perc"] = eng_high_perc

    # Rename "breakdown" to "TOTAL" in the first row
    if "breakdown" in df.columns:
        df.loc[0, "breakdown"] = "TOTAL"

    return df

def process_all_sheets(file_path):
    """
    Processes all sheets in an ODS file:
    - Applies the `process_sheet` function to each sheet.
    - Concatenates the results into a single DataFrame.
    """
    # Load all sheets from the ODS file
    sheets = pd.read_excel(file_path, sheet_name=None, engine="odf")

    results = []
    for sheet_name, df in sheets.items():
        processed_sheet = process_sheet(sheet_name, df)
        if processed_sheet is not None:
            results.append(processed_sheet)

    # Concatenate results
    if results:
        final_result = pd.concat(results, ignore_index=True)
    else:
        final_result = pd.DataFrame()  # Empty DataFrame if no sheets are processed

    return final_result

# File paths
input_file_path = "cls.ods"  # Replace with your file path


# Process the file and save the result
final_data = process_all_sheets(input_file_path)

In [ ]:
# Add in column for if above/below England Average
final_data["above_below"] = final_data.apply(
    lambda row: 1 if row["2023/24 Lower Estimate percentage (%)"] > row["eng_low_perc"] else
                -1 if row["2023/24 Upper Estimate percentage (%)"] < row["eng_high_perc"] else 0,
                axis = 1
)

final_data['distance_from_england'] = final_data['2023/24 Percentage (%)'] - final_data['eng_perc']
final_data['std'] = final_data.groupby('text')['2023/24 Percentage (%)'].transform('std')
final_data['z_score'] = (final_data['distance_from_england'])/final_data['std']

exclude_colnames = ['LAD23 code', 'text', 'answer', 'breakdown', 'ITL1 code', 'ITL2 code', 'ITL2 name']
result = {}
for _, row in final_data.iterrows():
    district = row['LAD23 code']
    key =  f"{row['text']} :: {row['answer']}"
    values = {col: row[col]
            for col in final_data.columns if col not in exclude_colnames
        }
    if district not in result :
        result[district] = {}
    result[district][key] = values

with open("output.json", "w") as f:
    json.dump(result, f)

In [57]:
neighbourhood = final_data.loc[final_data["text"] == "To what extent would you agree or disagree that people in your neighbourhood pull together to improve the neighbourhood?"]
final_data

6                     Question Response Breakdown  2023/24 Percentage (%)  \
0     Local authority district                Adur               5.483361   
1     Local authority district        Amber Valley               4.746419   
2     Local authority district                Arun               4.062442   
3     Local authority district            Ashfield              11.981989   
4     Local authority district             Ashford               4.225282   
...                        ...                 ...                    ...   
9467  Local authority district            Worthing              40.434066   
9468  Local authority district            Wychavon              36.973515   
9469  Local authority district                Wyre               36.17503   
9470  Local authority district         Wyre Forest              37.966492   
9471  Local authority district                York              48.240982   

6    2023/24 Lower Estimate percentage (%)  \
0                                 3.568646   
1                                 3.016628   
2                                 2.448169   
3                                 8.498893   
4                                 2.541654   
...                                    ...   
9467                              34.84576   
9468                             31.487915   
9469                             31.414275   
9470                             33.197797   
9471                             43.008692   

6    2023/24 Upper Estimate percentage (%) 2023/24 Number of respondents  \
0                                 8.336581                            24   
1                                 7.392499                            22   
2                                 6.668372                            18   
3                                16.633073                            41   
4                                   6.9447                            18   
...                                    ...                           ...   
9467                             46.281965                           203   
9468                             42.817523                           212   
9469                             41.223617                           206   
9470                             42.979468                           202   
9471                             53.512131                           244   

6    2023/24 Unweighted Base - number of people aged 16 and over LAD23 code  \
0                                                   486           E07000223   
1                                                   460           E07000032   
2                                                   492           E07000224   
3                                                   436           E07000170   
4                                                   468           E07000105   
...                                                 ...                 ...   
9467                                                481           E07000229   
9468                                                487           E07000238   
9469                                                509           E07000128   
9470                                                513           E07000239   
9471                                                478           E06000014   

6                                          ITL2 name ITL2 code  ...  \
0                       Surrey, East and West Sussex      TLJ2  ...   
1                     Derbyshire and Nottinghamshire      TLF1  ...   
2                       Surrey, East and West Sussex      TLJ2  ...   
3                     Derbyshire and Nottinghamshire      TLF1  ...   
4                                               Kent      TLJ4  ...   
...                                              ...       ...  ...   
9467                    Surrey, East and West Sussex      TLJ2  ...   
9468  Herefordshire, Worcestershire and Warwickshire      TLG1  ...   
9469                 

In [58]:
m = folium.Map()
folium.GeoJson(la_geo, name = "hello_world").add_to(m)

folium.Choropleth(
    geo_data = la_geo,
    name = "choloropleth",
    data = neighbourhood,
    columns = ['LAD23 code', 'z_score'],
    key_on = 'feature.properties.LAD24CD',
    fill_color="YlGn",
    legend_name = "civic engagement tricile"
).add_to(m)
m.save("out.html")
m